# Homework: Phrasal Chunking

This is your documentation for the chunker homework.

In [1]:
import numpy as np 
import pandas as pd 
import itertools 
import smtplib
import perc
import default
import sys
from collections import defaultdict
import gzip # use compressed data files
import copy, operator, optparse, sys, os
import re 
import time

In [57]:
feat_vec = {}
tagset = []
train_data = []

tagset = perc.read_tagset("data/tagset.txt")
train_data = perc.read_labeled_data("data/train.txt.gz", "data/train.feats.gz", verbose=False)
print("reading data ...", file=sys.stderr)

reading data ...


In [61]:
def perc_train(train_data, tagset, numepochs):
    t1=time.time()
    FEATURE_VEC_SENT=[] 
    FEATURE_DIC={}
    
    default_tag=tagset[0]
    
    e=0
    
    ## For every epoch
    for epoch in range(numepochs) : 
        print("epoch {}".format(e))
        
        sent_ind=0
        
        
        ## For every sentence
        for (sent_labels,sent_features) in train_data : 

            
            ## Argmax tags for all words in current sentence
            argmax_tag=perc.perc_test(FEATURE_DIC, sent_labels, sent_features, tagset, default_tag)       
            
            labels = copy.deepcopy(sent_labels)
            labels.insert(0, '_B-1 _B-1 _B-1')
            labels.insert(0, '_B-2 _B-2 _B-2') # first two 'words' are _B-2 _B-1
            labels.append('_B+1 _B+1 _B+1')
            labels.append('_B+2 _B+2 _B+2') # last two 'words' are _B+1 _B+2  
            N = len(labels)   
            
            
            ## for each word
            feat_index=0
            j=0
            
            
            ## For every word
            for i in range(2, N-2):
                
                (feat_index, feats) = perc.feats_for_word(feat_index, sent_features)  
                fields = labels[i].split()    
                
                
                word = fields[0]
                actual_tag=fields[2]    
                
                #print("word_index = {}, word = {}, actual_tag = {}, argmax_tag= {}".format(i,word,actual_tag,argmax_tag[i]))
                
                amax_tag=argmax_tag[j]
                
                local_keys=list(FEATURE_DIC.keys())
                feat_list=[(x,actual_tag,amax_tag) for x in feats]
                #print(feat_list)
                
                for (f,b,c) in feat_list :  
                    
                    if b!=c : 
                        
                        if (f,b) in local_keys : 
                            FEATURE_DIC[(f,b)]=FEATURE_DIC[(f,b)]+(e+1)/2
                        else : 
                            FEATURE_DIC[(f,b)]=(e+1)/2  
                    
                        if (f,c) in local_keys : 
                            FEATURE_DIC[(f,c)]=FEATURE_DIC[(f,c)]-(e+1)/2
                        else : 
                            FEATURE_DIC[(f,c)]=-(e+1)/2

                            
                            
                j=j+1                 
              
            sent_ind=sent_ind+1  
            print(FEATURE_DIC)          
    
        
        e=e+1
        
        
    print("Training finished in ",time.time()-t1)
    return FEATURE_DIC
                
            
            

print('training of {} sentences begin'.format(N))
feat_vec = perc_train(train_data, tagset, 5)
perc.perc_write_to_file(feat_vec, "default.model")
print("wrote model to disk")

training of 5000 sentences begin
epoch 0
{('U00:_B-2', 'B-NP'): 1, ('U01:_B-1', 'B-NP'): 1, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 1, ('U04:the', 'B-NP'): 1, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 1, ('U11:_B-1', 'B-NP'): 1, ('U12:NNq', 'B-NP'): 1, ('U13:IN', 'B-NP'): -3, ('U14:DT', 'B-NP'): -1, ('U15:_B-2/_B-1', 'B-NP'): 1, ('U16:_B-1/NN', 'B-NP'): 1, ('U17:NN/IN', 'B-NP'): -1, ('U18:IN/DT', 'B-NP'): 1, ('U20:_B-2/_B-1/NN', 'B-NP'): 1, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 1, ('B', 'B-NP'): -17, ('U00:_B-1', 'B-PP'): 1, ('U00:_B-1', 'B-NP'): -1, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 1, ('U02:in', 'B-NP'): -1, ('U03:the', 'B-PP'): 1, ('U03:the', 'B-NP'): -1, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 1, ('U06:in/the', 'B-NP'): -1, ('U10:_B-1', 'B-PP'): 1, ('

{('U00:_B-2', 'B-NP'): 2, ('U01:_B-1', 'B-NP'): 2, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 1, ('U04:the', 'B-NP'): 2, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 2, ('U11:_B-1', 'B-NP'): 2, ('U12:NNq', 'B-NP'): 5, ('U13:IN', 'B-NP'): -1, ('U14:DT', 'B-NP'): 1, ('U15:_B-2/_B-1', 'B-NP'): 2, ('U16:_B-1/NN', 'B-NP'): 1, ('U17:NN/IN', 'B-NP'): 1, ('U18:IN/DT', 'B-NP'): 3, ('U20:_B-2/_B-1/NN', 'B-NP'): 1, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 3, ('B', 'B-NP'): 14, ('U00:_B-1', 'B-PP'): 1, ('U00:_B-1', 'B-NP'): 1, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 3, ('U02:in', 'B-NP'): -1, ('U03:the', 'B-PP'): 6, ('U03:the', 'B-NP'): -1, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 1, ('U06:in/the', 'B-NP'): -1, ('U10:_B-1', 'B-PP'): 1, ('U10:_B-1', 'B-NP'): 1, ('U11:NN', 'B-PP'): 7,

{('U00:_B-2', 'B-NP'): 4, ('U01:_B-1', 'B-NP'): 4, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 2, ('U04:the', 'B-NP'): 3, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 4, ('U11:_B-1', 'B-NP'): 4, ('U12:NNq', 'B-NP'): 7, ('U13:IN', 'B-NP'): 0, ('U14:DT', 'B-NP'): 3, ('U15:_B-2/_B-1', 'B-NP'): 4, ('U16:_B-1/NN', 'B-NP'): 1, ('U17:NN/IN', 'B-NP'): 2, ('U18:IN/DT', 'B-NP'): 4, ('U20:_B-2/_B-1/NN', 'B-NP'): 1, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 4, ('B', 'B-NP'): 32, ('U00:_B-1', 'B-PP'): 1, ('U00:_B-1', 'B-NP'): 1, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 5, ('U02:in', 'B-NP'): -1, ('U03:the', 'B-PP'): 9, ('U03:the', 'B-NP'): -1, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 2, ('U06:in/the', 'B-NP'): -1, ('U10:_B-1', 'B-PP'): 1, ('U10:_B-1', 'B-NP'): 1, ('U11:NN', 'B-PP'): 12,

{('U00:_B-2', 'B-NP'): 6, ('U01:_B-1', 'B-NP'): 6, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 2, ('U04:the', 'B-NP'): 4, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 6, ('U11:_B-1', 'B-NP'): 6, ('U12:NNq', 'B-NP'): 7, ('U13:IN', 'B-NP'): 0, ('U14:DT', 'B-NP'): 5, ('U15:_B-2/_B-1', 'B-NP'): 6, ('U16:_B-1/NN', 'B-NP'): 1, ('U17:NN/IN', 'B-NP'): 2, ('U18:IN/DT', 'B-NP'): 4, ('U20:_B-2/_B-1/NN', 'B-NP'): 1, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 4, ('B', 'B-NP'): 42, ('U00:_B-1', 'B-PP'): 0, ('U00:_B-1', 'B-NP'): 2, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 6, ('U02:in', 'B-NP'): -1, ('U03:the', 'B-PP'): 10, ('U03:the', 'B-NP'): -1, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 2, ('U06:in/the', 'B-NP'): -1, ('U10:_B-1', 'B-PP'): 0, ('U10:_B-1', 'B-NP'): 2, ('U11:NN', 'B-PP'): 13

{('U00:_B-2', 'B-NP'): 4, ('U01:_B-1', 'B-NP'): 4, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 2, ('U04:the', 'B-NP'): 4, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 4, ('U11:_B-1', 'B-NP'): 4, ('U12:NNq', 'B-NP'): 8, ('U13:IN', 'B-NP'): 0, ('U14:DT', 'B-NP'): 3, ('U15:_B-2/_B-1', 'B-NP'): 4, ('U16:_B-1/NN', 'B-NP'): 1, ('U17:NN/IN', 'B-NP'): 2, ('U18:IN/DT', 'B-NP'): 4, ('U20:_B-2/_B-1/NN', 'B-NP'): 1, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 4, ('B', 'B-NP'): 49, ('U00:_B-1', 'B-PP'): 1, ('U00:_B-1', 'B-NP'): 2, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 9, ('U02:in', 'B-NP'): -1, ('U03:the', 'B-PP'): 10, ('U03:the', 'B-NP'): -1, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 2, ('U06:in/the', 'B-NP'): -1, ('U10:_B-1', 'B-PP'): 1, ('U10:_B-1', 'B-NP'): 2, ('U11:NN', 'B-PP'): 16

...

{('U00:_B-2', 'B-NP'): 12, ('U01:_B-1', 'B-NP'): 12, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 3, ('U04:the', 'B-NP'): 3, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 12, ('U11:_B-1', 'B-NP'): 12, ('U12:NNq', 'B-NP'): 24, ('U13:IN', 'B-NP'): 4, ('U14:DT', 'B-NP'): 2, ('U15:_B-2/_B-1', 'B-NP'): 12, ('U16:_B-1/NN', 'B-NP'): 2, ('U17:NN/IN', 'B-NP'): 6, ('U18:IN/DT', 'B-NP'): 2, ('U20:_B-2/_B-1/NN', 'B-NP'): 2, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 5, ('B', 'B-NP'): 136, ('U00:_B-1', 'B-PP'): 2, ('U00:_B-1', 'B-NP'): 8, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 22, ('U02:in', 'B-NP'): -2, ('U03:the', 'B-PP'): 20, ('U03:the', 'B-NP'): -4, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 8, ('U06:in/the', 'B-NP'): -2, ('U10:_B-1', 'B-PP'): 2, ('U10:_B-1', 'B-NP'): 8, ('U11:NN', 'B-

{('U00:_B-2', 'B-NP'): 13, ('U01:_B-1', 'B-NP'): 13, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 3, ('U04:the', 'B-NP'): 3, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 13, ('U11:_B-1', 'B-NP'): 13, ('U12:NNq', 'B-NP'): 25, ('U13:IN', 'B-NP'): 4, ('U14:DT', 'B-NP'): 4, ('U15:_B-2/_B-1', 'B-NP'): 13, ('U16:_B-1/NN', 'B-NP'): 2, ('U17:NN/IN', 'B-NP'): 6, ('U18:IN/DT', 'B-NP'): 2, ('U20:_B-2/_B-1/NN', 'B-NP'): 2, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 5, ('B', 'B-NP'): 146, ('U00:_B-1', 'B-PP'): 2, ('U00:_B-1', 'B-NP'): 9, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 23, ('U02:in', 'B-NP'): -2, ('U03:the', 'B-PP'): 20, ('U03:the', 'B-NP'): -4, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 8, ('U06:in/the', 'B-NP'): -2, ('U10:_B-1', 'B-PP'): 2, ('U10:_B-1', 'B-NP'): 9, ('U11:NN', 'B-

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



{('U00:_B-2', 'B-NP'): 25, ('U01:_B-1', 'B-NP'): 25, ('U02:Confidence', 'B-NP'): 1, ('U03:in', 'B-NP'): 3, ('U04:the', 'B-NP'): 4, ('U05:_B-1/Confidence', 'B-NP'): 1, ('U06:Confidence/in', 'B-NP'): 1, ('U10:_B-2', 'B-NP'): 25, ('U11:_B-1', 'B-NP'): 25, ('U12:NNq', 'B-NP'): 29, ('U13:IN', 'B-NP'): 5, ('U14:DT', 'B-NP'): 3, ('U15:_B-2/_B-1', 'B-NP'): 25, ('U16:_B-1/NN', 'B-NP'): 3, ('U17:NN/IN', 'B-NP'): 6, ('U18:IN/DT', 'B-NP'): 3, ('U20:_B-2/_B-1/NN', 'B-NP'): 3, ('U21:_B-1/NN/IN', 'B-NP'): 1, ('U22:NN/IN/DT', 'B-NP'): 5, ('B', 'B-NP'): 190, ('U00:_B-1', 'B-PP'): 2, ('U00:_B-1', 'B-NP'): 11, ('U01:Confidence', 'B-PP'): 1, ('U01:Confidence', 'B-NP'): -1, ('U02:in', 'B-PP'): 27, ('U02:in', 'B-NP'): -2, ('U03:the', 'B-PP'): 25, ('U03:the', 'B-NP'): -5, ('U04:pound', 'B-PP'): 1, ('U04:pound', 'B-NP'): -1, ('U05:Confidence/in', 'B-PP'): 1, ('U05:Confidence/in', 'B-NP'): -1, ('U06:in/the', 'B-PP'): 9, ('U06:in/the', 'B-NP'): -2, ('U10:_B-1', 'B-PP'): 2, ('U10:_B-1', 'B-NP'): 11, ('U11:NN', '

KeyboardInterrupt: 

In [38]:
feat_vec

{('U00:_B-2', 'B-NP'): 1,
 ('U01:_B-1', 'B-NP'): 1,
 ('U02:Confidence', 'B-NP'): 1,
 ('U03:in', 'B-NP'): 1,
 ('U04:the', 'B-NP'): 1,
 ('U05:_B-1/Confidence', 'B-NP'): 1,
 ('U06:Confidence/in', 'B-NP'): 1,
 ('U10:_B-2', 'B-NP'): 1,
 ('U11:_B-1', 'B-NP'): 1,
 ('U12:NNq', 'B-NP'): 1,
 ('U13:IN', 'B-NP'): -3,
 ('U14:DT', 'B-NP'): -1,
 ('U15:_B-2/_B-1', 'B-NP'): 1,
 ('U16:_B-1/NN', 'B-NP'): 1,
 ('U17:NN/IN', 'B-NP'): -1,
 ('U18:IN/DT', 'B-NP'): 1,
 ('U20:_B-2/_B-1/NN', 'B-NP'): 1,
 ('U21:_B-1/NN/IN', 'B-NP'): 1,
 ('U22:NN/IN/DT', 'B-NP'): 1,
 ('B', 'B-NP'): -17,
 ('U00:_B-1', 'B-PP'): 1,
 ('U00:_B-1', 'B-NP'): -1,
 ('U01:Confidence', 'B-PP'): 1,
 ('U01:Confidence', 'B-NP'): -1,
 ('U02:in', 'B-PP'): 1,
 ('U02:in', 'B-NP'): -1,
 ('U03:the', 'B-PP'): 1,
 ('U03:the', 'B-NP'): -1,
 ('U04:pound', 'B-PP'): 1,
 ('U04:pound', 'B-NP'): -1,
 ('U05:Confidence/in', 'B-PP'): 1,
 ('U05:Confidence/in', 'B-NP'): -1,
 ('U06:in/the', 'B-PP'): 1,
 ('U06:in/the', 'B-NP'): -1,
 ('U10:_B-1', 'B-PP'): 1,
 ('U10:_B

In [54]:
%%capture --no-stderr output
print("reading test data ...", file=sys.stderr)
test_data = perc.read_labeled_data("data/dev.txt", "data/dev.feats", verbose=False)
print("done.", file=sys.stderr)
feat_vec = perc.perc_read_from_file("default.model")
perc.perc_testall(feat_vec, test_data, tagset)

reading test data ...
done.


In [55]:
import score_chunks
boundary = "-X-" # something to use as boundary between sentences
outside = "O" # tag used to mark the outside of any chunk
conlleval = False # use conlleval (should be False for most use cases)
numfeats = 2 # number of columns to consider as features, typically "word POStag"
(test, _) = score_chunks.readTestFile(str(output), boundary, outside, conlleval, numfeats)
with open("data/reference500.txt") as f:
    (reference, _) = score_chunks.readTestFile(f.read(), boundary, outside, conlleval, numfeats)
print("Score: %.2f" % score_chunks.corpus_fmeasure(reference, test, False))

processed 500 sentences with 10375 tokens and 5783 phrases; found phrases: 4023; correct phrases: 1187
             ADJP: precision:   0.00%; recall:   0.00%; F1:   0.00; found:      0; correct:     99
             ADVP: precision:   8.74%; recall:   7.92%; F1:   8.31; found:    183; correct:    202
            CONJP: precision:   0.00%; recall:   0.00%; F1:   0.00; found:      0; correct:      5
             INTJ: precision:   0.00%; recall:   0.00%; F1:   0.00; found:      0; correct:      1
               NP: precision:  25.02%; recall:  18.04%; F1:  20.97; found:   2182; correct:   3026
               PP: precision:  47.29%; recall:  42.18%; F1:  44.59; found:   1089; correct:   1221
              PRT: precision:   0.00%; recall:   0.00%; F1:   0.00; found:      0; correct:     22
             SBAR: precision:   0.00%; recall:   0.00%; F1:   0.00; found:      0; correct:    107
               VP: precision:  19.33%; recall:  10.00%; F1:  13.18; found:    569; correct:   1100
accura

In [ ]:
str(output)

In [ ]:
x=['a','b','c']
y=[1,2]
list(itertools.product(x,y))

In [40]:
list(range(2, 37-2))

[2,
 3,
 4,
 5,
 6,
 7,
 8,
 9,
 10,
 11,
 12,
 13,
 14,
 15,
 16,
 17,
 18,
 19,
 20,
 21,
 22,
 23,
 24,
 25,
 26,
 27,
 28,
 29,
 30,
 31,
 32,
 33,
 34]